## Setting up file structure

In [4]:
import os

# Define the directory structure
dirs = [
    'images/train',
    'images/val',
    'labels/train',
    'labels/val'
]

# Create the directories
for dir in dirs:
    os.makedirs(dir, exist_ok=True)

In [5]:
yaml_content = """
path: C:/Users/tuypa/Desktop/TrashDnC
train: images/train
val: images/val
nc: 6
names: ['paper', 'plastic', 'metal', 'glass', 'other', 'unknown']
"""

with open('data.yaml', 'w') as file:
    file.write(yaml_content)

In [6]:
import os
import shutil
from glob import glob

# 🔥 Adjust this to your root TrashDnC directory
base_dir = r"C:\Users\tuypa\Desktop\TrashDnC"

# Paths to clean
paths_to_delete = [
    os.path.join(base_dir, "runs"),
    os.path.join(base_dir, "train.txt"),
    os.path.join(base_dir, "val.txt"),
    os.path.join(base_dir, "labels", "train"),
    os.path.join(base_dir, "labels", "val"),
    os.path.join(base_dir, "labels", "train.cache"),
    os.path.join(base_dir, "labels", "val.cache"),
]

for path in paths_to_delete:
    if os.path.isfile(path):
        os.remove(path)
        print(f"🧽 Deleted file: {path}")
    elif os.path.isdir(path):
        shutil.rmtree(path)
        print(f"🧽 Deleted folder: {path}")

# Recreate empty label folders
os.makedirs(os.path.join(base_dir, "labels", "train"), exist_ok=True)
os.makedirs(os.path.join(base_dir, "labels", "val"), exist_ok=True)
print("✅ Cleanup complete. Fresh label folders created.")


🧽 Deleted folder: C:\Users\tuypa\Desktop\TrashDnC\runs
🧽 Deleted file: C:\Users\tuypa\Desktop\TrashDnC\train.txt
🧽 Deleted file: C:\Users\tuypa\Desktop\TrashDnC\val.txt
🧽 Deleted folder: C:\Users\tuypa\Desktop\TrashDnC\labels\train
🧽 Deleted folder: C:\Users\tuypa\Desktop\TrashDnC\labels\val
🧽 Deleted file: C:\Users\tuypa\Desktop\TrashDnC\labels\train.cache
🧽 Deleted file: C:\Users\tuypa\Desktop\TrashDnC\labels\val.cache
✅ Cleanup complete. Fresh label folders created.


## Download YOLO architecture

In [14]:
!pip install ultralytics

   ---------------------------------------- 0.0/978.8 kB ? eta -:--:--
   -------------------------------- ------- 786.4/978.8 kB 5.6 MB/s eta 0:00:01
   ---------------------------------------- 978.8/978.8 kB 5.1 MB/s eta 0:00:00
   ---------------------------------------- 0.0/12.6 MB ? eta -:--:--
   -- ------------------------------------- 0.8/12.6 MB 11.2 MB/s eta 0:00:02
   ------ --------------------------------- 2.1/12.6 MB 5.9 MB/s eta 0:00:02
   ---------- ----------------------------- 3.1/12.6 MB 5.4 MB/s eta 0:00:02
   ----------- ---------------------------- 3.7/12.6 MB 4.2 MB/s eta 0:00:03
   -------------- ------------------------- 4.5/12.6 MB 4.2 MB/s eta 0:00:02
   ---------------- ----------------------- 5.2/12.6 MB 4.0 MB/s eta 0:00:02
   ------------------- -------------------- 6.0/12.6 MB 3.9 MB/s eta 0:00:02
   -------------------- ------------------- 6.3/12.6 MB 3.9 MB/s eta 0:00:02
   --------------------- ------------------ 6.8/12.6 MB 3.6 MB/s eta 0:00:02
   --

## Download the TACO Dataset

In [31]:
!git clone https://github.com/pedropro/TACO.git

Cloning into 'TACO'...


In [ ]:
!cd TACO && python download.py

## Split data to train

In [5]:
import os
import shutil
import random

# === PATH SETUP ===
base_path = "C:/Users/tuypa/Desktop/TrashDnC"
all_images_path = os.path.join(base_path, "new_data", "all_images")
all_labels_path = os.path.join(base_path, "new_data", "all_labels")
images_train_path = os.path.join(base_path, "images", "train")
images_val_path = os.path.join(base_path, "images", "val")
labels_train_path = os.path.join(base_path, "labels", "train")
labels_val_path = os.path.join(base_path, "labels", "val")

# === CLEAN OLD TRAIN/VAL SPLITS ===
for path in [images_train_path, images_val_path, labels_train_path, labels_val_path]:
    if os.path.exists(path):
        shutil.rmtree(path)
    os.makedirs(path)

# === MATCH IMAGES AND LABELS ===
image_files = [f for f in os.listdir(all_images_path) if f.lower().endswith(('.jpg', '.jpeg', '.png'))]
paired_files = []

for img_file in image_files:
    label_file = os.path.splitext(img_file)[0] + ".txt"
    if os.path.exists(os.path.join(all_labels_path, label_file)):
        paired_files.append((img_file, label_file))

# === SHUFFLE AND SPLIT 80/20 ===
random.shuffle(paired_files)
split_index = int(0.8 * len(paired_files))
train_pairs = paired_files[:split_index]
val_pairs = paired_files[split_index:]

# === COPY FILES TO SPLIT FOLDERS ===
def copy_pairs(pairs, img_dst, lbl_dst):
    for img_file, lbl_file in pairs:
        shutil.copy(os.path.join(all_images_path, img_file), os.path.join(img_dst, img_file))
        shutil.copy(os.path.join(all_labels_path, lbl_file), os.path.join(lbl_dst, lbl_file))

copy_pairs(train_pairs, images_train_path, labels_train_path)
copy_pairs(val_pairs, images_val_path, labels_val_path)

print(f"✅ YOLOv8 Data Prep Done! {len(train_pairs)} train / {len(val_pairs)} val samples.")

✅ YOLOv8 Data Prep Done! 314 train / 79 val samples.


## Augmentation

In [3]:
!pip install albumentations opencv-python

In [2]:
import os
import random
import shutil
from collections import Counter
from glob import glob

import albumentations as A
import cv2

# Paths
images_dir = r"C:\Users\tuypa\Desktop\TrashDnC\new_data\all_images"
labels_dir = r"C:\Users\tuypa\Desktop\TrashDnC\new_data\all_labels"
output_images_dir = r"C:\Users\tuypa\Desktop\TrashDnC\balanced_data\images"
output_labels_dir = r"C:\Users\tuypa\Desktop\TrashDnC\balanced_data\labels"

os.makedirs(output_images_dir, exist_ok=True)
os.makedirs(output_labels_dir, exist_ok=True)

# Augmentation pipeline
augment = A.Compose([
    A.HorizontalFlip(p=0.5),
    A.RandomBrightnessContrast(p=0.3),
    A.ShiftScaleRotate(shift_limit=0.05, scale_limit=0.05, rotate_limit=10, p=0.5)
], bbox_params=A.BboxParams(format='yolo', label_fields=['class_labels']))

# Count current class instances
class_counts = Counter()
label_files = glob(os.path.join(labels_dir, "*.txt"))

for label_path in label_files:
    with open(label_path, "r") as f:
        for line in f:
            class_id = line.strip().split()[0]
            class_counts[class_id] += 1

# Target count = max of existing classes
max_class = max(class_counts, key=class_counts.get)
max_count = class_counts[max_class]
print("📊 Class counts before balancing:", class_counts)
print("🎯 Target per class:", max_count)

# Existing images (base names without extension)
existing_images = set(os.path.splitext(f)[0] for f in os.listdir(output_images_dir) if f.endswith(".jpg"))

# Process and augment
for label_path in label_files:
    filename = os.path.basename(label_path).replace(".txt", "")
    img_path = os.path.join(images_dir, filename + ".jpg")
    if not os.path.exists(img_path):
        continue

    # Copy original image/label if not already done
    if filename not in existing_images:
        shutil.copy(img_path, os.path.join(output_images_dir, filename + ".jpg"))
        shutil.copy(label_path, os.path.join(output_labels_dir, filename + ".txt"))
        existing_images.add(filename)

    # Read original label
    with open(label_path, "r") as f:
        labels = f.readlines()

    bboxes = [list(map(float, line.strip().split()[1:])) for line in labels]
    class_labels = [line.strip().split()[0] for line in labels]

    img = cv2.imread(img_path)

    # Count how many augmentations already exist for this image
    for class_id in set(class_labels):
        current_count = class_counts[class_id]
        if current_count >= max_count:
            continue

        num_needed = max_count - current_count

        # Check how many existing augmentations we have
        existing_augs = len([name for name in existing_images if name.startswith(f"{filename}_aug_")])
        to_generate = max(0, num_needed - existing_augs)

        for i in range(existing_augs, existing_augs + to_generate):
            transformed = augment(image=img, bboxes=bboxes, class_labels=class_labels)
            aug_img = transformed["image"]
            aug_bboxes = transformed["bboxes"]
            aug_labels = transformed["class_labels"]

            new_name = f"{filename}_aug_{i}"
            aug_img_path = os.path.join(output_images_dir, new_name + ".jpg")
            aug_label_path = os.path.join(output_labels_dir, new_name + ".txt")

            cv2.imwrite(aug_img_path, aug_img)
            with open(aug_label_path, "w") as f:
                for lbl, bbox in zip(aug_labels, aug_bboxes):
                    f.write(f"{lbl} {' '.join(map(str, bbox))}\n")

            existing_images.add(new_name)
            class_counts[class_id] += 1

print("✅ Dataset balanced and saved to:", output_images_dir)

C:\Python312\Lib\site-packages\albumentations\core\validation.py:87: UserWarning: ShiftScaleRotate is a special case of Affine transform. Please use Affine transform instead.
  original_init(self, **validated_kwargs)


📊 Class counts before balancing: Counter({'4': 298, '2': 142, '3': 104, '1': 94, '5': 46, '0': 27})
🎯 Target per class: 298
✅ Dataset balanced and saved to: C:\Users\tuypa\Desktop\TrashDnC\balanced_data\images


In [3]:
import os
import shutil
import random
from glob import glob

# Input: balanced dataset
image_dir = r"C:\Users\tuypa\Desktop\TrashDnC\balanced_data\images"
label_dir = r"C:\Users\tuypa\Desktop\TrashDnC\balanced_data\labels"

# Output: YOLO structure (already exists)
train_img_dir = r"C:\Users\tuypa\Desktop\TrashDnC\images\train"
val_img_dir = r"C:\Users\tuypa\Desktop\TrashDnC\images\val"
train_lbl_dir = r"C:\Users\tuypa\Desktop\TrashDnC\labels\train"
val_lbl_dir = r"C:\Users\tuypa\Desktop\TrashDnC\labels\val"

# Clear old data
for folder in [train_img_dir, val_img_dir, train_lbl_dir, val_lbl_dir]:
    for file in os.listdir(folder):
        os.remove(os.path.join(folder, file))

# Get all images
image_paths = glob(os.path.join(image_dir, "*.jpg"))
random.shuffle(image_paths)

# Split 80/20
split_idx = int(0.8 * len(image_paths))
train_imgs = image_paths[:split_idx]
val_imgs = image_paths[split_idx:]

def copy_pairs(img_list, img_out_dir, lbl_out_dir):
    for img_path in img_list:
        file = os.path.basename(img_path)
        lbl = file.replace(".jpg", ".txt")
        lbl_path = os.path.join(label_dir, lbl)

        shutil.copy(img_path, os.path.join(img_out_dir, file))
        if os.path.exists(lbl_path):
            shutil.copy(lbl_path, os.path.join(lbl_out_dir, lbl))

copy_pairs(train_imgs, train_img_dir, train_lbl_dir)
copy_pairs(val_imgs, val_img_dir, val_lbl_dir)

print("✅ Balanced dataset has been split and saved to images/labels train/val folders.")

✅ Balanced dataset has been split and saved to images/labels train/val folders.


### removing old test cache before retraining

In [20]:
import os

os.remove(r"C:\Users\tuypa\Desktop\TrashDnC\labels\train.cache")
os.remove(r"C:\Users\tuypa\Desktop\TrashDnC\labels\val.cache")

## Reduce amount of images and Split data

In [18]:
import os
import shutil
import random
from collections import defaultdict

# 🛠️ Paths
balanced_dir = r"C:\Users\tuypa\Desktop\TrashDnC\balanced_data"
images_dir = os.path.join(balanced_dir, "images")
labels_dir = os.path.join(balanced_dir, "labels")

final_root = r"C:\Users\tuypa\Desktop\TrashDnC"
train_img_dir = os.path.join(final_root, "images", "train")
val_img_dir = os.path.join(final_root, "images", "val")
train_lbl_dir = os.path.join(final_root, "labels", "train")
val_lbl_dir = os.path.join(final_root, "labels", "val")

# 📦 Create folders
for path in [train_img_dir, val_img_dir, train_lbl_dir, val_lbl_dir]:
    os.makedirs(path, exist_ok=True)

# 🎯 Target
TARGET_TOTAL_IMAGES = 2000
SPLIT_RATIO = 0.8  # 80% train, 20% val

# Step 1: Group by class
class_to_files = defaultdict(list)

for label_file in os.listdir(labels_dir):
    label_path = os.path.join(labels_dir, label_file)
    with open(label_path, "r") as f:
        lines = f.readlines()
        if not lines:
            continue
        first_class = lines[0].strip().split()[0]
        class_to_files[first_class].append(label_file)

# Step 2: Sample
num_classes = len(class_to_files)
samples_per_class = TARGET_TOTAL_IMAGES // num_classes

all_selected = []

for class_id, files in class_to_files.items():
    selected = random.sample(files, min(len(files), samples_per_class))
    all_selected.extend(selected)

random.shuffle(all_selected)

# Step 3: Train/Val split
split_index = int(len(all_selected) * SPLIT_RATIO)
train_files = all_selected[:split_index]
val_files = all_selected[split_index:]

# Step 4: Move files
def copy_files(file_list, image_dest, label_dest):
    for label_file in file_list:
        image_file = label_file.replace(".txt", ".jpg")

        src_img = os.path.join(images_dir, image_file)
        src_lbl = os.path.join(labels_dir, label_file)

        dst_img = os.path.join(image_dest, image_file)
        dst_lbl = os.path.join(label_dest, label_file)

        if os.path.exists(src_img) and os.path.exists(src_lbl):
            shutil.copy2(src_img, dst_img)
            shutil.copy2(src_lbl, dst_lbl)

copy_files(train_files, train_img_dir, train_lbl_dir)
copy_files(val_files, val_img_dir, val_lbl_dir)

# ✅ Summary
print(f"\n✅ Reduced and split dataset saved to:")
print(f" - Train: {len(train_files)} images")
print(f" - Val  : {len(val_files)} images")
print(f"\n📁 Images train: {train_img_dir}")
print(f"📁 Labels train: {train_lbl_dir}")
print(f"📁 Images val  : {val_img_dir}")
print(f"📁 Labels val  : {val_lbl_dir}")


✅ Reduced and split dataset saved to:
 - Train: 1537 images
 - Val  : 385 images

📁 Images train: C:\Users\tuypa\Desktop\TrashDnC\images\train
📁 Labels train: C:\Users\tuypa\Desktop\TrashDnC\labels\train
📁 Images val  : C:\Users\tuypa\Desktop\TrashDnC\images\val
📁 Labels val  : C:\Users\tuypa\Desktop\TrashDnC\labels\val


## Launch Training

In [21]:
import subprocess

# Define the YOLOv8 training command
command = [
    "yolo", "task=detect", "mode=train",
    "data=C:/Users/tuypa/Desktop/TrashDnC/data.yaml",
    "model=yolov8n.pt",
    "epochs=50",
    "imgsz=416",
    "batch=8",
    "workers=2",
    "name=TrashDnC_exp3"
]

# Launch training process
process = subprocess.Popen(
    command,
    stdout=subprocess.PIPE,
    stderr=subprocess.STDOUT,
    text=True,
    encoding="utf-8"  # Fix UnicodeDecodeError
)

# Read and log the output
log_path = "train_log.txt"
with open(log_path, "w", encoding="utf-8") as log_file:
    for line in process.stdout:
        print(line, end="")
        log_file.write(line)

print(f"\n✅ Training completed. Log saved to: {log_path}")

New https://pypi.org/project/ultralytics/8.3.114 available 😃 Update with 'pip install -U ultralytics'
Ultralytics 8.3.111 🚀 Python-3.12.1 torch-2.5.1+cu121 CUDA:0 (NVIDIA GeForce RTX 3070 Laptop GPU, 8192MiB)
engine\trainer: task=detect, mode=train, model=yolov8n.pt, data=C:/Users/tuypa/Desktop/TrashDnC/data.yaml, epochs=50, time=None, patience=100, batch=8, imgsz=416, save=True, save_period=-1, cache=False, device=None, workers=2, project=None, name=TrashDnC_exp3, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=N